In [218]:
import pandas as pd 
import numpy as np
pd.set_option('display.max_columns', 500)
pd.set_option('display.max_rows', 500)
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split
from sklearn.linear_model import Ridge

In [238]:
train_main = pd.read_csv("../data/task1/train_1.7.csv", encoding="cp1251")
test_main = pd.read_csv("../data/task1/test_1.9.csv", encoding="cp1251")

train_aux_coords = pd.read_csv("../data/task1_additional/coords_train_1.1.csv", encoding="cp1251")
test_aux_coords = pd.read_csv("../data/task1_additional/coords_train_1.1.csv", encoding="cp1251")

train_aux_frac = pd.read_csv("../data/task1_additional/frac_train_1.csv", encoding="cp1251")
test_aux_frac = pd.read_csv("../data/task1_additional/frac_test_1.csv", encoding="cp1251")

train_aux_gdis = pd.read_csv("../data/task1_additional/gdis_train1.2.csv", encoding="cp1251")
test_aux_gdis = pd.read_csv("../data/task1_additional/gdis_test1.2.csv", encoding="cp1251")

In [239]:
target_column = "Нефть, т"
y_train = train_main[target_column]

In [240]:
ids = ["Скважина"]
text = ["Причина простоя"," Куст","Состояние на конец месяца", "Причина простоя.1", "Примечание", "Мероприятия", ]
categorical = ["Тип скважины","Неустановившийся режим","ГТМ", "Метод","Характер работы", "Состояние", "Агент закачки", "Пласт МЭР", "Способ эксплуатации", "Тип насоса", 
              "Состояние на конец месяца", "Номер бригады", "Фонтан через насос", "Нерентабельная" "Неустановившийся режим", "Назначение по проекту",
              "Группа фонда","Тип дополнительного оборудования","Тип газосепаратора", "Марка ПЭД","Тип ГЗУ","ДНС","КНС",
              "Нерентабельная", "Куст"]
dates = ["Дата", "Дата ГРП","Время до псевдоуст-ся режима", "Дата запуска после КРС", "Дата пуска", "Дата останова","Дата ввода в эксплуатацию"]
combined = set(ids+text+categorical+dates)
all_cmns = set(train_main.columns)
continious = list(all_cmns - combined)
# find columns where all values are nans
non_useful_columns = []
for c in train_main.columns:
    null_columns = train_main[train_main[c].isnull()]
    if len(null_columns)== len(train_main):
        non_useful_columns.append(c)
# find columns absent in test
absent_columns = list(set(train_main.columns) - set(test_main.columns))
#delete target absent and null columns from train
train_main.drop([target_column]+absent_columns+non_useful_columns, axis=1, inplace=True)
test_main.drop(non_useful_columns, inplace=True, axis=1)
train_main.head()

Скважина        Дата  ГТМ Метод Характер работы  \
0  53514b4c4150ad897d82dd7d42cfc1a5  2012-11-30  0.0   ЭЦН             НЕФ   
1  53514b4c4150ad897d82dd7d42cfc1a5  2013-12-01  0.0   ЭЦН             НЕФ   
2  53514b4c4150ad897d82dd7d42cfc1a5  2014-12-01  NaN   NaN             NaN   
3  53514b4c4150ad897d82dd7d42cfc1a5  2012-12-31  0.0   ЭЦН             НЕФ   
4  53514b4c4150ad897d82dd7d42cfc1a5  2014-01-01  0.0   ЭЦН             НЕФ   

  Состояние  Время работы, ч  Время накопления  Попутный газ, м3  Закачка, м3  \
0      РАБ.            744.0               0.0           24577.0          0.0   
1      РАБ.            741.0               0.0           22893.0          0.0   
2       NaN              NaN               NaN               NaN          NaN   
3      РАБ.            696.0               0.0           23799.0          0.0   
4      РАБ.            672.0               0.0           21172.0          0.0   

   Природный газ, м3  Газ из газовой шапки, м3  Конденсат, т  Простой, ч  \
0                0.0                       0.0           0.0         0.0   
1                0.0                       0.0           0.0         3.0   
2                NaN                       NaN           NaN         NaN   
3                0.0                       0.0           0.0         0.0   
4                0.0                       0.0           0.0         0.0   

    Причина простоя Приемистость, м3/сут Обводненность (вес), % Агент закачки  \
0               NaN                    0                   35,2           NaN   
1  Геологич.причина                    0                   42,1           NaN   
2               NaN                  NaN                    NaN           NaN   
3               NaN                    0                   35,3           NaN   
4               NaN                    0                   41,3           NaN   

   Дебит конденсата Добыча растворенного газа, м3  \
0               0.0                      24576,93   
1               0.0                      22893,44   
2               NaN                           NaN   
3               0.0                      23798,79   
4               0.0                      21171,91   

  Дебит попутного газа, м3/сут                         Пласт МЭР Куст  \
0                        792,8  9a64c83d6572681a661112d916442cea   19   
1                       741,49  9a64c83d6572681a661112d916442cea   19   
2                          NaN  9a64c83d6572681a661112d916442cea   19   
3                       820,65  9a64c83d6572681a661112d916442cea   19   
4                       756,14  9a64c83d6572681a661112d916442cea   19   

           Тип скважины  Диаметр экспл.колонны  Диаметр НКТ  Диаметр штуцера  \
0  Наклонно-направленно                  146.8         67.4              0.0   
1  Наклонно-направленно                  146.8         67.4              0.0   
2  Наклонно-направленно                  146.8         67.4              0.0   
3  Наклонно-направленно                  146.8         67.4              0.0   
4  Наклонно-направленно                  146.8         67.4              0.0   

   Глубина верхних дыр перфорации  Удлинение Способ эксплуатации  \
0                          2387.0      34.84                 ЭЦН   
1                          2387.0      34.84                 ЭЦН   
2                          2387.0      34.84                 ЭЦН   
3                          2387.0      34.84                 ЭЦН   
4                          2387.0      34.84                 ЭЦН   

     Тип насоса  Производительность ЭЦН   Напор  Частота  \
0  ВНН5-59-2450                    60.0  2460.0     50.0   
1  ВНН5-59-2450                    60.0  2460.0     50.0   
2  ВНН5-59-2450                    60.0  2460.0     52.0   
3  ВНН5-59-2450                    60.0  2460.0     50.0   
4  ВНН5-59-2450                    60.0  2460.0     50.0   

   Коэффициент сепарации  Глубина спуска  Буферное давление  Давление в линии  \
0                    0.7          231

In [241]:
def get_if_column_exists(df, columns):
    exists = list(set(columns)&set(df.columns))
    return df[exists]
train_cont = get_if_column_exists(train_main, continious)

In [242]:
train_cat = get_if_column_exists(train_main, categorical)

In [243]:
def get_float(v):
    v = str(v)
    if v != "NaN":
        new = v.replace(",",".")
        return float(new)
    return v
incorrect_float_cols = ["Обводненность (вес), %","Приемистость, м3/сут", "Дебит попутного газа, м3/сут", "Добыча растворенного газа, м3"]
for c in incorrect_float_cols:
    train_cont[c]=train_cont[c].apply(get_float)

/anaconda2/envs/env/lib/python3.6/site-packages/ipykernel/__main__.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


In [244]:
train_cont.fillna(train_cont.mean(), inplace=True)
train_cont.isnull().values.any()

/anaconda2/envs/env/lib/python3.6/site-packages/pandas/core/generic.py:5434: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._update_inplace(new_data)


False

In [245]:
train_cont.drop(y_train[y_train.isnull()].index, inplace=True)
y_train = y_train[~y_train.isnull()].apply(get_float)
len(y_train) == len(train_cont)

/anaconda2/envs/env/lib/python3.6/site-packages/pandas/core/frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


True

In [246]:
X_train_cont_final, X_val_cont, y_train_final, y_val = train_test_split(train_cont, y_train, test_size=0.2, random_state=42)

In [247]:
ridge = Ridge()
ridge.fit(X_train_cont_final, y_train_final)

Ridge(alpha=1.0, copy_X=True, fit_intercept=True, max_iter=None,
   normalize=False, random_state=None, solver='auto', tol=0.001)

In [248]:
y_pred=ridge.predict(X_val_cont)

In [254]:
import numpy as np

def mean_absolute_percentage_error(y_true, y_pred): 
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    null_idx = y_true==0
    y_true[null_idx]=y_true[null_idx]+1
    y_pred[null_idx]=y_pred[null_idx]+1
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

In [264]:
mean_absolute_percentage_error(y_val, y_pred)

985.5780570741524

In [259]:
!pip install xgboost

    100% |████████████████████████████████| 604kB 1.9MB/s ta 0:00:011
  Running setup.py bdist_wheel for xgboost ... done
  Stored in directory: /Users/kkushaev/Library/Caches/pip/wheels/82/2d/9a/d9014a0add86cdad990022418a905ca9e93948ee8862ae755d
Successfully built xgboost
mkl-random 1.0.1 requires cython, which is not installed.
mkl-fft 1.0.4 requires cython, which is not installed.
implicit 0.3.6 requires h5py, which is not installed.
You are using pip version 10.0.1, however version 18.0 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


In [262]:
from xgboost import XGBRegressor
regressor = XGBRegressor()
regressor.fit(X_train_cont_final, y_train_final)
y_pred_xgb = regressor.predict(X_test_cont)

In [263]:
y_pred_xgb

array([ 1.03982593e+03,  4.65167618e+00,  3.58393994e+03,  3.80641602e+02,
        1.52641739e+02,  2.07180572e+00,  2.57353210e+02,  8.15330994e+02,
        1.57309143e+02,  6.48073273e+01,  5.40351501e+02,  4.65167618e+00,
        6.36084747e+00,  1.19518234e+02,  4.65167618e+00,  2.99395111e+02,
        3.67759277e+02,  1.05860791e+03,  4.65167618e+00,  2.54734146e+02,
        1.53962677e+02,  2.24116333e+02,  2.37631653e+02,  3.62435746e+00,
        4.65167618e+00,  2.07180572e+00,  3.68705170e+02,  1.50621887e+03,
        3.99832458e+02,  2.07180572e+00,  1.22302600e+03,  2.07180572e+00,
        3.23724884e+02,  5.80769348e+02,  1.90695847e+02,  1.03835083e+03,
        4.38401550e+02,  2.07180572e+00,  9.03598267e+02,  4.22193939e+02,
        3.76712463e+02,  5.34256653e+02,  3.90499634e+02,  6.58168579e+02,
        2.70886658e+02,  2.07180572e+00,  1.94477020e+02,  1.68991241e+02,
        3.62435746e+00,  2.08104385e+02,  1.17846954e+02,  1.48569962e+02,
        2.06331741e+02,  

In [265]:
mean_absolute_percentage_error(y_val, y_pred_xgb)

113.62026986986619

In [292]:
sample = pd.read_csv("../data/sample_task2.csv")
sample.head()

0     1
0  0  83.0
1  1  79.0
2  2  82.0
3  3  86.0
4  4  79.0

In [293]:
sample.columns

Index(['0', '1'], dtype='object')

In [294]:
X_train_cont_final

Коэффициент продуктивности  Давление наcыщения  Закачка, м3  \
2087                    0.567031          123.400000          0.0   
2495                    0.285037           98.916081        234.0   
3109                    0.224940          112.000000          0.0   
422                     0.320438           80.900000          0.0   
2464                    0.069961          123.400000          0.0   
2118                    0.285037           98.916081       2774.0   
3129                    0.285037           98.916081          0.0   
1721                    0.285037           98.916081         20.0   
971                     0.285037           98.916081          0.0   
2927                    0.084917           80.000000          0.0   
3121                    0.000000          112.000000          0.0   
3112                    0.119340          112.000000          0.0   
288                     0.285037           98.916081          0.0   
1065                    0.108186           80.000000          0.0   
678                     0.285037           98.916081          0.0   
2528                    0.054293          123.400000          0.0   
1562                    0.285037           98.916081        810.0   
405                     0.408465           80.900000          0.0   
3111                    0.000000          112.000000          0.0   
1104                    0.285037           98.916081        143.0   
2079                    0.228291          123.400000          0.0   
694                     0.043425          145.000000          0.0   
2026                    0.285037           98.916081          0.0   
1331                    0.285037           98.916081          0.0   
3181                    0.471635          112.000000          0.0   
1127                    0.285037           98.916081          0.0   
2594                    0.511297           80.000000          0.0   
2392                    0.285037           98.916081          0.0   
776                     0.285037           98.916081       3075.0   
1238                    0.033828           80.000000          0.0   
1922                    0.119246          123.400000          0.0   
2466                    0.285037           98.916081        276.0   
2371                    0.285037           98.916081          0.0   
3276                    0.401237          117.000000          0.0   
1878                    0.285037           98.916081        161.0   
1973                    0.148115           80.000000          0.0   
2107                    0.343808          123.400000          0.0   
1463                    0.285037           98.916081          0.0   
159                     0.285037           98.916081          0.0   
1026                    0.518875          118.000000          0.0   
3118                    0.257142          112.000000          0.0   
473                     0.591765           80.900000          0.0   
2526                    0.121289           80.000000          0.0   
2947                    0.059218           80.000000          0.0   
1044                    0.503344          118.000000          0.0   
570                     0.285037           98.916081          0.0   
2044                    0.285037           98.916081          0.0   
397                     0.285037           98.916081          0.0   
2251                    0.285037           98.916081       3926.0   
347                     0.285037           98.916081          0.0   
2338                    0.285037           98.916081          0.0   
689                     0.091396          145.000000          0.0   
3245                    0.285037           98.916081          0.0   
745                     0.133573          145.000000          0.0   
1952                    0.180738          123.400000          0.0   
268                     0.441796           80.900000          0.0   
3337                    0.352207          112.000000          0.0   
2419

In [295]:
new_frame = X_train_cont_final.multiply(X_train_cont_final)
new_frame

Коэффициент продуктивности  Давление наcыщения  Закачка, м3  \
2087                3.215247e-01         15227.56000          0.0   
2495                8.124606e-02          9784.39111      54756.0   
3109                5.059793e-02         12544.00000          0.0   
422                 1.026804e-01          6544.81000          0.0   
2464                4.894488e-03         15227.56000          0.0   
2118                8.124606e-02          9784.39111    7695076.0   
3129                8.124606e-02          9784.39111          0.0   
1721                8.124606e-02          9784.39111        400.0   
971                 8.124606e-02          9784.39111          0.0   
2927                7.210872e-03          6400.00000          0.0   
3121                0.000000e+00         12544.00000          0.0   
3112                1.424193e-02         12544.00000          0.0   
288                 8.124606e-02          9784.39111          0.0   
1065                1.170419e-02          6400.00000          0.0   
678                 8.124606e-02          9784.39111          0.0   
2528                2.947763e-03         15227.56000          0.0   
1562                8.124606e-02          9784.39111     656100.0   
405                 1.668433e-01          6544.81000          0.0   
3111                0.000000e+00         12544.00000          0.0   
1104                8.124606e-02          9784.39111      20449.0   
2079                5.211668e-02         15227.56000          0.0   
694                 1.885688e-03         21025.00000          0.0   
2026                8.124606e-02          9784.39111          0.0   
1331                8.124606e-02          9784.39111          0.0   
3181                2.224400e-01         12544.00000          0.0   
1127                8.124606e-02          9784.39111          0.0   
2594                2.614249e-01          6400.00000          0.0   
2392                8.124606e-02          9784.39111          0.0   
776                 8.124606e-02          9784.39111    9455625.0   
1238                1.144343e-03          6400.00000          0.0   
1922                1.421965e-02         15227.56000          0.0   
2466                8.124606e-02          9784.39111      76176.0   
2371                8.124606e-02          9784.39111          0.0   
3276                1.609912e-01         13689.00000          0.0   
1878                8.124606e-02          9784.39111      25921.0   
1973                2.193792e-02          6400.00000          0.0   
2107                1.182041e-01         15227.56000          0.0   
1463                8.124606e-02          9784.39111          0.0   
159                 8.124606e-02          9784.39111          0.0   
1026                2.692314e-01         13924.00000          0.0   
3118                6.612188e-02         12544.00000          0.0   
473                 3.501861e-01          6544.81000          0.0   
2526                1.471095e-02          6400.00000          0.0   
2947                3.506759e-03          6400.00000          0.0   
1044                2.533550e-01         13924.00000          0.0   
570                 8.124606e-02          9784.39111          0.0   
2044                8.124606e-02          9784.39111          0.0   
397                 8.124606e-02          9784.39111          0.0   
2251                8.124606e-02          9784.39111   15413476.0   
347                 8.124606e-02          9784.39111          0.0   
2338                8.124606e-02          9784.39111          0.0   
689                 8.353309e-03         21025.00000          0.0   
3245                8.124606e-02          9784.39111          0.0   
745                 1.784180e-02         21025.00000          0.0   
1952                3.266624e-02         15227.56000          0.0   
268                 1.951833e-01          6544.81000          0.0   
3337                1.240498e-01         12544.00000          0.0   
2419

In [296]:
y

(2064, 77)